In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms, models
import os

In [5]:
## Building the dataset

import os
import shutil
import random

def split_data(class_name, split_ratio=0.8):
    src_dir = f'./{class_name}'
    if not os.path.exists(src_dir):
        print(f"Source folder {src_dir} does not exist!")
        return

    # Include all files (ignore extensions)
    files = [f for f in os.listdir(src_dir) if os.path.isfile(os.path.join(src_dir, f))]
    print(f"Found {len(files)} files in {class_name}")

    if len(files) == 0:
        print(f"No files found in {src_dir}")
        return

    random.shuffle(files)
    split_idx = int(len(files) * split_ratio)
    train_files = files[:split_idx]
    val_files = files[split_idx:]

    for split, split_files in [('train', train_files), ('val', val_files)]:
        dst_dir = os.path.join('dataset', split, class_name)
        os.makedirs(dst_dir, exist_ok=True)
        for file in split_files:
            src_file = os.path.join(src_dir, file)
            dst_file = os.path.join(dst_dir, file)
            print(f"Copying {src_file} to {dst_file}")
            shutil.copy(src_file, dst_file)

split_data('demented')
split_data('non-demented')


Found 86 files in demented
Copying ./demented/OAS2_0159_MR2 to dataset/train/demented/OAS2_0159_MR2
Copying ./demented/OAS2_0108_MR1 to dataset/train/demented/OAS2_0108_MR1
Copying ./demented/OAS2_0144_MR1 to dataset/train/demented/OAS2_0144_MR1
Copying ./demented/OAS2_0176_MR3 to dataset/train/demented/OAS2_0176_MR3
Copying ./demented/OAS2_0184_MR2 to dataset/train/demented/OAS2_0184_MR2
Copying ./demented/OAS2_0102_MR3 to dataset/train/demented/OAS2_0102_MR3
Copying ./demented/OAS2_0139_MR2 to dataset/train/demented/OAS2_0139_MR2
Copying ./demented/OAS2_0165_MR1 to dataset/train/demented/OAS2_0165_MR1
Copying ./demented/OAS2_0172_MR1 to dataset/train/demented/OAS2_0172_MR1
Copying ./demented/OAS2_0140_MR3 to dataset/train/demented/OAS2_0140_MR3
Copying ./demented/OAS2_0172_MR2 to dataset/train/demented/OAS2_0172_MR2
Copying ./demented/OAS2_0127_MR2 to dataset/train/demented/OAS2_0127_MR2
Copying ./demented/OAS2_0182_MR1 to dataset/train/demented/OAS2_0182_MR1
Copying ./demented/OAS2_

In [3]:
from PIL import Image
import os

def custom_loader(path):
    print(f"Loading image: {path}")  # Debugging output

    # Fix file extension issue
    if path.endswith('.jpg.rf'):
        path = path[:-7] + '.jpg'

    try:
        img = Image.open(path).convert('RGB')  # Ensure image is in RGB format
        return img
    except Exception as e:
        print(f"Error loading image {path}: {e}")
        return None


In [4]:
# Define data transformations for data augmentation and normalization
data_transforms = {
    'train': transforms.Compose([
        transforms.RandomResizedCrop(224),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    'val': transforms.Compose([
        transforms.Resize(256),
        transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
}

In [5]:
# Define the data directory
data_dir = 'dataset'

# Create data loaders
image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x), data_transforms[x], loader=custom_loader) for x in ['train', 'val']}
#image_datasets


In [6]:
dataloaders = {x: torch.utils.data.DataLoader(image_datasets[x], batch_size=2, shuffle=True, num_workers=0) for x in ['train', 'val']}
dataset_sizes = {x: len(image_datasets[x]) for x in ['train', 'val']}
print(dataset_sizes)

class_names = image_datasets['train'].classes
class_names

{'train': 6370, 'val': 364}


['daisy', 'dandelion']

In [7]:
# Load the pre-trained ResNet-18 model
model = models.resnet50(pretrained=True)

# Freeze all layers except the final classification layer
for name, param in model.named_parameters():
    if "fc" in name:  # Unfreeze the final classification layer
        param.requires_grad = True
    else:
        param.requires_grad = False

# Define the loss function and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)  # Use all parameters


# Move the model to the GPU if available
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
model = model.to(device)


C:\Users\omana\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
C:\Users\omana\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to C:\Users\omana/.cache\torch\hub\checkpoints\resnet50-0676ba61.pth
100%|██████████| 97.8M/97.8M [00:05<0

In [48]:
# Training loop
num_epochs = 10
for epoch in range(num_epochs):
    for phase in ['train', 'val']:
        if phase == 'train':
            model.train()
        else:
            model.eval()

        running_loss = 0.0
        running_corrects = 0

        for inputs, labels in dataloaders[phase]:
            inputs = inputs.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()

            with torch.set_grad_enabled(phase == 'train'):
                outputs = model(inputs)
                _, preds = torch.max(outputs, 1)
                loss = criterion(outputs, labels)

                if phase == 'train':
                    loss.backward()
                    optimizer.step()

            running_loss += loss.item() * inputs.size(0)
            running_corrects += torch.sum(preds == labels.data)

        epoch_loss = running_loss / dataset_sizes[phase]
        epoch_acc = running_corrects.double() / dataset_sizes[phase]

        print(f'{phase} Loss: {epoch_loss:.4f} Acc: {epoch_acc:.4f}')

print("Training complete!")


Loading image: dataset\train\dandelion\22196426956_eca94f6faa_m_jpg.rf.d3c4a4adc6a2f7ee5640004577f04f50.jpg
Loading image: dataset\train\dandelion\3589816063_50f8de7b64_m_jpg.rf.872bd69abe02b8ef42981ffedee70950.jpg
Loading image: dataset\train\dandelion\6901435398_b3192ff7f8_m_jpg.rf.ccad3b12a50bccf9c8f95b2275736bf1.jpg
Loading image: dataset\train\dandelion\4571681134_b605a61547_n_jpg.rf.c03fda00b892d56d1dc77895a6e67443.jpg
Loading image: dataset\train\daisy\3310644753_5607eb96a4_m_jpg.rf.24f1dc910896f0a1bdddb15069f9407c.jpg
Loading image: dataset\train\daisy\2646438199_b309cffd65_n_jpg.rf.a2557d6b9fc0323c7af7984960eb8a3a.jpg
Loading image: dataset\train\dandelion\8717787983_c83bdf39fe_n_jpg.rf.a9eabfd93a288f487e3f0b0a7937ceee.jpg
Loading image: dataset\train\daisy\5722473541_ffac1ae67e_n_jpg.rf.68bccb0b13b1d8653de83e01af431fc8.jpg
Loading image: dataset\train\daisy\299129811_d6ebda9970_jpg.rf.6a8e6218f5494ec3aa721aa3d6b814ca.jpg
Loading image: dataset\train\dandelion\16462263826_2555

In [49]:
# Save the model
torch.save(model.state_dict(), 'flower_classification_model.pth')

In [42]:
import os
import concurrent.futures
from PIL import Image

dataset_path = "dataset/train"  # Change this to your dataset path
num_threads = os.cpu_count()  # Use all CPU cores

def check_and_remove_image(file_path):
    """Verifies image and removes it if corrupted."""
    try:
        with Image.open(file_path) as img:
            img.verify()  # Verify without fully loading
    except Exception:
        print(f"Removing corrupted image: {file_path}")
        os.remove(file_path)  # Delete invalid image

# Get all image file paths from subdirectories
image_files = []
for root, _, files in os.walk(dataset_path):
    for file in files:
        image_files.append(os.path.join(root, file))

# Run in parallel for speed
with concurrent.futures.ThreadPoolExecutor(max_workers=num_threads) as executor:
    executor.map(check_and_remove_image, image_files)

print("✅ Image cleanup complete!")


Removing corrupted image: dataset/train\daisy\4534460263_8e9611db3c_n_jpg.rf.2756de378a7a041406b7aa661912da99.jpg
✅ Image cleanup complete!


In [43]:
del image_datasets, dataloaders  # Clear previous dataset objects

## Classification on unseen image

In [51]:
import torch
from torchvision import models, transforms
from PIL import Image

# Load the saved model
model = models.resnet18(pretrained=True)
model.fc = nn.Linear(model.fc.in_features, 1000) 
model.load_state_dict(torch.load("flower_classification_model.pth"))
model.eval()

# Create a new model with the correct final layer
new_model = models.resnet18(pretrained=True)
new_model.fc = nn.Linear(new_model.fc.in_features, 2)

# Copy the weights and biases from the loaded model to the new model
new_model.fc.weight.data = model.fc.weight.data[0:2] # Copy only the first 2 output units
new_model.fc.bias.data = model.fc.bias.data[0:2]

C:\Users\omana\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
C:\Users\omana\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [53]:
# load and preprocess unseen image
image_path = 'test.jpg'
image = Image.open(image_path)
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])

input_tensor = preprocess(image)
input_batch = input_tensor.unsqueeze(0) # Add a batch dimension

In [54]:
# Perform inference
with torch.no_grad():
    output = model(input_batch)

# Get the predicted class
_, predicted_class = output.max(1)

# Map the predicted class to the class name
class_names = ['daisy', 'dandelion']
predicted_class_name = class_names[predicted_class.item()]

print(f'The predicted class is: {predicted_class_name}')

The predicted class is: daisy


In [3]:
import numpy as np

file_path = "/home/omanaokar/Desktop/Alzeimers-detection/demented/OAS2_0102_MR1"

file = np.load(file_path)
file.shape

(20, 256, 115)